# Import modules

In [1]:
import numpy as np
import importlib
import mdtraj as md
import matplotlib.pyplot as plt
from sklearn.decomposition import PCA, KernelPCA
# Import visualization module for molecular visualization
from tools.visualization import Visualization
# Import descriptors module to obtain descriptors for triad molecule
from tools.descriptors import Descriptors
# Import plotting module for plotting
from tools import plotting

# Load files

In [2]:
file_dir = '/xspace/hl4212/DURF_datasets/triad_molecule'
traj_path = f'{file_dir}/triad_dataset.nc'
top_path = f'{file_dir}/triad_forcefield_ground.prmtop'

# Data visualization

In [3]:
triad_viz = Visualization(traj_path, top_path)
triad_viz.ball_and_stick()

NGLWidget(max_frame=99999)

## Compare different conformations

In [5]:
triad_viz.compare(23348, 44865)

NGLWidget()

# Get descriptors

In [6]:
d = Descriptors(traj_path, top_path)
EuclidianDist_1 = d.eucdist('C33','C128')
Angle_1 = d.angle('C33','C96','C128')
Angle_2 = d.angle('C33','C69','C96')
Angle_3 = d.angle('C69','C96','C128')
Dihedral_1 = d.dihedral('C21','C61','C66','C65')
Dihedral_2 = d.dihedral('C89','N6','C95','C96')
# For the RMSD descriptor, choose the frame with the largest 'Angle_1' as linear, the smallest as bent
# The frame number for linear is 88213, for bent is 29685
RMSD_Linear = d.rmsd(frame = 88213)
RMSD_Bent = d.rmsd(frame = 29685)

In [7]:
# Visulize the descriptors in dataframe
d_DataFrame = d.to_df(EuclidianDist_1=EuclidianDist_1, Angle_1=Angle_1,\
                      Angle_2=Angle_2, Angle_3=Angle_3, Dihedral_1=Dihedral_1,\
                      Dihedral_2=Dihedral_2, RMSD_Linear =RMSD_Linear, RMSD_Bent =RMSD_Bent)
d_DataFrame.iloc[88213, :]

EuclidianDist_1    4.680938
Angle_1            3.102149
Angle_2            2.592577
Angle_3            2.856325
Dihedral_1         1.394683
Dihedral_2         2.993495
RMSD_Linear        0.000000
RMSD_Bent          1.464485
Name: 88213, dtype: float32

In [7]:
# Convert dataframe to nparray for dimensionality reduction and save it back to disk
results_dir = '/xspace/hl4212/durf_hq/projects/Gustave_Li/Main_program/results/Newer_version'
array_path = f'{results_dir}/descriptors_arr'
d_array = np.array(d_DataFrame)
np.save(array_path, d_array)

# [Dimensionality reduction](Dimensionality_reduction.py) (Run on hpc)

## Dimreduct for descriptors (reduce to 2 dimensions)
- PCA
- kPCA
- kernel = poly, rbf
- t\-SNE, default setting
    - perlexity = 30
    - learning_rate = 200
    - init = random
- t\-SNE, hyperparameters tuned to the recommendation in [this paper](https://www.nature.com/articles/s41467-019-13056-x)
    - perplexity = 30
    - learning_rate = (size_of_data)//12
    - init = pca
- MDS is not used since the dataset is too large for the algorithm to run

## Dimreduct for coordinates
- Since hpc has no `mdtraj` module installed, first generate the traj xyz in 2D for the dimreduct program

In [40]:
# Load the original dataset for dim reduction of the coordinates
file_dir = '/xspace/hl4212/DURF_datasets/triad_molecule'
traj_path = f'{file_dir}/triad_dataset.nc'
top_path = f'{file_dir}/triad_forcefield_ground.prmtop'
traj = md.load(traj_path, top=top_path)

# Superpose the trajectory to minimize the translational and rotational difference of each configuration

traj = traj.superpose(traj, frame = 0)
    
# Reshape the xyz coordinates to 2D
xyz = traj.xyz.reshape([len(traj.xyz), (traj.xyz.size//len(traj.xyz))])

# Save it to disk
xyz_dir = '/gpfsnyu/scratch/hl4212'
xyz_path = f'{xyz_dir}/xyz_aligned.npy'
np.save(xyz_path, xyz)

# Visualization of the dimreduct results

In [14]:
importlib.reload(plotting)
pca = np.load(f'{results_dir}/dimreduct_PCA.npy')
plotting.dimreduct('pca', pca)

Loading BokehJS ...

In [15]:
kpca = np.load(f'{results_dir}/dimreduct_kPCA_rbf.npy')
plotting.dimreduct("kpca_rbf", kpca)

Loading BokehJS ...

In [8]:
kpca = np.load(f'{results_dir}/dimreduct_kPCA_poly.npy')
plotting.dimreduct("kpca_poly", kpca)

Loading BokehJS ...

In [21]:
tsne_std = np.load(f'{results_dir}/dimreduct_tsne_standard.npy')
plotting.dimreduct("dimreduct_tsne_standard", tsne_std)

Loading BokehJS ...

In [22]:
tsne_optm = np.load(f'{results_dir}/dimreduct_tsne_optimized.npy')
plotting.dimreduct("dimreduct_tsne_optimized", tsne_optm)

Loading BokehJS ...

In [34]:
triad_viz.compare(62538, 40465)

NGLWidget()

In [41]:
pca_tsne_xyz = np.load(f'{results_dir}/dimreduct_PCA_tSNE_xyz_wierd.npy')
plotting.dimreduct("pca_tsne_xyz", pca_tsne_xyz)

Loading BokehJS ...